In [2]:
import pyspark
from pyspark.sql import SparkSession
from pyspark.conf import SparkConf
from pyspark.context import SparkContext
from config_variables import var_credentials_location, var_gcs_connector
import requests
import pandas as pd
from io import StringIO


Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


In [3]:
conf = SparkConf() \
    .setMaster('local[*]') \
    .setAppName('GCS Ingestion') \
    .set("spark.jars", var_gcs_connector) \
    .set("spark.hadoop.google.cloud.auth.service.account.enable", "true") \
    .set("spark.hadoop.google.cloud.auth.service.account.json.keyfile", var_credentials_location)

In [4]:
#  Configuring Hadoop

sc = SparkContext(conf=conf)

hadoop_conf = sc._jsc.hadoopConfiguration()

hadoop_conf.set("fs.AbstractFileSystem.gs.impl",  "com.google.cloud.hadoop.fs.gcs.GoogleHadoopFS")
hadoop_conf.set("fs.gs.impl", "com.google.cloud.hadoop.fs.gcs.GoogleHadoopFileSystem")
hadoop_conf.set("fs.gs.auth.service.account.json.keyfile", var_credentials_location)
hadoop_conf.set("fs.gs.auth.service.account.enable", "true")

23/08/02 15:40:05 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).


In [5]:
# Initialising Spark Session
spark = SparkSession.builder \
    .config(conf=sc.getConf()) \
    .getOrCreate()

In [7]:
base_url = r"https://cycling.data.tfl.gov.uk/ActiveTravelCountsProgramme/1-Strategic%20counts%20(CIO)"

# 2015-Central.csv
year = 2015
area = "Central"

url = f'{base_url}/{year}-{area}.csv'


In [9]:
try:
    response = requests.get(url)
    csv_data = response.content.decode('utf-8')
except requests.exceptions.RequestException as e:
    print(f"Error downloading data from {url}: {e}")

csv_file = StringIO(csv_data)
df = spark.read.csv(csv_data, header=True, inferSchema=True)

df.show()

AnalysisException: [PATH_NOT_FOUND] Path does not exist: file:/Users/arithfonseka/Documents/github_repos/project_1/notebooks/Year,UnqID,Date,Weather,Time,Day,Round,Dir,Path,Mode,Count
2015,CENCY001,04/06/2015,Dry,06:00:00,Weekday,A,Northbound,n/a,Private cycles,3
2015,CENCY001,04/06/2015,Dry,06:15:00,Weekday,A,Northbound,n/a,Private cycles,10
2015,CENCY001,04/06/2015,Dry,06:30:00,Weekday,A,Northbound,n/a,Private cycles,18
2015,CENCY001,04/06/2015,Dry,06:45:00,Weekday,A,Northbound,n/a,Private cycles,39
2015,CENCY001,04/06/2015,Dry,07:00:00,Weekday,A,Northbound,n/a,Private cycles,65
2015,CENCY001,04/06/2015,Dry,07:15:00,Weekday,A,Northbound,n/a,Private cycles,83
2015,CENCY001,04/06/2015,Dry,07:30:00,Weekday,A,Northbound,n/a,Private cycles,118
2015,CENCY001,04/06/2015,Dry,07:45:00,Weekday,A,Northbound,n/a,Private cycles,153
2015,CENCY001,04/06/2015,Dry,08:00:00,Weekday,A,Northbound,n/a,Private cycles,165
2015,CENCY001,04/06/2015,Dry,08:15:00,Weekday,A,Northbound,n/a,Private cycl